In [1]:
# libraries forworking with data
import numpy as np
import pandas as pd
import pandas_profiling as pp

# scikit-learn libraries
from sklearn.model_selection import StratifiedKFold, cross_val_score, GridSearchCV, RandomizedSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
from sklearn.ensemble import BaggingClassifier
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier
from sklearn.metrics import roc_auc_score

# XGBoost Classifier
from xgboost import XGBClassifier

# Additional libraries
from scipy.stats import rankdata
from os import cpu_count
n_jobs = cpu_count() - 1

In [2]:
# input data
train = pd.read_csv('../data/train_modulbank.csv', sep='\t').drop('Unnamed: 0', axis=1)
test = pd.read_csv('../data/test_modulbank.csv', sep='\t').drop('Unnamed: 0', axis=1)

In [3]:
# amount of data
train.shape, test.shape

((30500, 346), (4166, 346))

In [4]:
# data report (commented) 
#train_report = pp.ProfileReport(train)
#test_report = pp.ProfileReport(test)

In [32]:
train_report

In [33]:
test_report

In [5]:
def get_float_part(data, latest_col=False):
    '''This function selects columns whose datatypes are float64'''
    data_ = data.copy()
    dop_columns = [str(max(list(map(int, data_.columns))) + i + 1) for i in range(2)]
    for column in dop_columns:
        data_[column] = 0.0
    float_cols = [i for i in data_.columns[1:] if np.dtype(data_[i]).name == 'float64']
    data_new = data_[float_cols]
    data_ = data_new.drop(dop_columns, axis=1)
    return (data_new if latest_col else data_) 

In [6]:
def new_features(min_, max_, data, ):
    '''This function concatenates some binary features in one feature'''
    res = ''
    for i in range(min_, max_):
        res += str(data[i])
    return res

In [7]:
def get_binary_grouped_intervals(data):
    '''This function returns continuous intervals of binary features'''
    data_ = data.copy()
    onehotencoding = []
    data_float = get_float_part(data_, latest_col=True)
    min_ = 0
    max_ = int(data_float.columns[0])
    for iter_ in data_float.columns[1:]:
        len_ = max_ - min_ - 1
        if len_ >= 2:
            onehotencoding.append((min_ + 1, min_ + len_ + 1))
        min_ = max_
        max_ = int(iter_)
    return onehotencoding

In [8]:
def get_binary_grouped_features(data, coding_columns):
    '''This function concatenates dataframe with new features'''
    new_columns = pd.DataFrame()
    redundant_cols = []
    for columns in coding_columns:
        cols = [str(i) for i in range(*columns)]
        new_columns[str(columns[0]) + '_'] = data[cols].apply(
            lambda x: new_features(0, columns[1] - columns[0], x), axis=1)
        redundant_cols += cols
    return new_columns, redundant_cols

In [9]:
def OneHot_training(columns):
    '''This function returns list of one-hot encoders'''
    encoders = []
    for column in columns:
        enc = OneHotEncoder()
        enc.fit(pd.DataFrame(columns[column]))
        encoders.append(enc)
    return encoders

In [10]:
def Label_training(columns):
    '''This function returns list of label encoders'''
    encoders = []
    for column in columns.columns:
        keys = {}
        for n_, value in zip(range(columns[column].nunique()), columns[column].unique()):
            keys.update({value: n_})
        encoders.append(keys)
    return encoders

In [11]:
def encoding_transform(columns, encoders, for_tree):
    '''This function transforms categorical features'''
    res = pd.DataFrame()
    for column, encoder in zip(columns, encoders):
        to_transform = pd.DataFrame(columns[column])
        if for_tree:
            res[column] = to_transform[column].apply(lambda x: encoder.get(x))
        else:
            data = encoder.transform(to_transform).toarray()
            columns_names = [column + str(i + 1) for i in range(len(data[0]))]
            new = pd.DataFrame(data.astype('int64'), columns=columns_names)
            res = pd.concat([res, new], axis=1)
    return res

In [12]:
def encoding(data, encoding_cols, encoders, for_tree):
    '''This function concatenates dataframe with encoded features'''
    data_ = data.copy()
    encoding_columns = encoding_transform(encoding_cols, encoders, for_tree)
    return pd.concat([data_, encoding_columns], axis=1)

In [13]:
def reindexing(list_, axis=1):
    '''This function re-indexes the dataframes columns'''
    size = len(list_)
    res = {}
    for i, column in zip(range(size), list_):
        res.update({column: (str(i) if axis==1 else i)})
    return res

In [14]:
# constant features on the test
conditions = {0:['129', '130', '137', '138', '140', '141', '149', 
                 '150', '164', '178', '186', '188', '192', '193',
                 '291', '301', '303', '305', '5'], 
              1:['11']}
# highly correlated and almost zero features
redundant_cols = ['191', '182', '185', '181', '172', '170', '157', '136', '135', '180', '22', '26', '2', '160', '152']
# reduntant features
redundant_cols += list(conditions.values())[0] + list(conditions.values())[1]

In [15]:
def get_subframe(df, conditions):
    '''This f
    unction returns subframe thaе meets the conditions'''
    data_ = df.copy()
    for value, columns in conditions.items():
        for column in columns:
            data_ = data_[data_[column]==value]
    data_.reset_index(drop=True, inplace=True)
    return data_

In [16]:
def get_intervals(intervals, n_ = 3):
    '''This function splits continious binary intervals'''
    inters = [(1, 5), (6, 10), (302, 306)]
    for interval in intervals:
        if interval[1] - interval[0] > 10:
            min_ = interval[0]
            max_ = interval[1]
            while min_ + n_ <= max_:
                inters.append((min_, min_ + n_))
                min_ += n_
    return inters

In [17]:
def preprocessing(data, encoders, for_tree=True):
    '''This function makes preprocessing'''
    data_ = data.copy()
    if encoders == None:
        data_ = get_subframe(data_, conditions)
    data_.drop(redundant_cols, axis=1, inplace=True)
    data_.rename(columns=reindexing(data_.columns), inplace=True)
    intervals = get_binary_grouped_intervals(data_)
    intervals = get_intervals(intervals)
    new_columns, redundant_columns = get_binary_grouped_features(data_, intervals)
    if encoders == None:
        encoders = (Label_training(new_columns) if for_tree else OneHot_training(new_columns))
    data_ = encoding(data_, new_columns, encoders, for_tree)
    data_.reset_index(drop=True, inplace=True)
    data_.rename(columns=reindexing(data_.columns), inplace=True)
    return data_, encoders

In [18]:
# make train and test preprocessing for logistic regression and decisions trees
for_tree = False
train_log, encoders = preprocessing(train, encoders=None, for_tree=for_tree)
test_log, _ = preprocessing(test, encoders, for_tree=for_tree)

for_tree = True
train_tree, encoders = preprocessing(train, encoders=None, for_tree=for_tree)
test_tree, _ = preprocessing(test, encoders, for_tree=for_tree)

In [19]:
#pp.ProfileReport(train_)

In [20]:
# amount of data
train_log.shape, test_log.shape, train_tree.shape, test_tree.shape

((30377, 605), (4166, 605), (30377, 373), (4166, 373))

In [21]:
# 5 samples from new train
train_log.sample(5)

0  1  2  3  4         5  6  7  8  9 ...   595  596  597  598  599  600  \
1272   0  1  0  0  0  0.090909  0  0  1  1 ...     0    0    1    0    0    0   
29392  0  0  0  0  0  0.090909  0  1  1  0 ...     1    0    1    0    0    0   
1257   0  1  0  0  0  0.090909  0  0  1  1 ...     0    0    1    0    0    0   
5661   0  1  0  1  0  0.090909  0  0  1  1 ...     0    0    1    0    0    0   
22680  0  1  0  1  0  0.090909  0  0  1  1 ...     0    0    1    0    0    0   

       601  602  603  604  
1272     1    0    0    0  
29392    1    0    0    0  
1257     1    0    0    0  
5661     1    0    0    0  
22680    1    0    0    0  

[5 rows x 605 columns]

In [22]:
# 5 samples from new test
test_log.sample(5)

0  1  2  3  4         5  6  7  8  9 ...   595  596  597  598  599  600  \
2648 NaN  1  0  0  0  0.090909  0  0  1  1 ...     1    0    1    0    0    0   
160  NaN  1  0  1  0  0.090909  0  0  1  1 ...     0    0    1    0    0    0   
3074 NaN  1  0  0  0  0.090909  0  0  1  1 ...     0    1    1    0    0    0   
1448 NaN  1  0  1  0  0.090909  0  0  1  1 ...     0    0    1    0    0    0   
2664 NaN  1  0  1  0  0.090909  0  0  1  1 ...     0    0    1    0    0    0   

      601  602  603  604  
2648    1    0    0    0  
160     1    0    0    0  
3074    1    0    0    0  
1448    1    0    0    0  
2664    1    0    0    0  

[5 rows x 605 columns]

In [23]:
def save_submission(prediction, filename):
    '''This function makes a submission files'''
    submission = pd.Series (prediction, name='_VAL_' )
    submission.to_csv(filename, index_label='_ID_', header =True )

### Cross-validation

In [24]:
# cross-validation 
skf = StratifiedKFold(n_splits=21, random_state=11)

## Logistic regression

In [25]:
X = train_log.drop('0', axis=1)
y = train_log['0']

In [26]:
lg = LogisticRegression(class_weight='balanced', dual=True)
parameters = {'C': [0.03],
              'max_iter': [125, 100] }
grid_search = GridSearchCV(lg, parameters, scoring ='roc_auc', cv=skf, verbose=1, error_score=1, n_jobs=n_jobs)
grid_search = grid_search.fit(X, y)

Fitting 21 folds for each of 2 candidates, totalling 42 fits


[Parallel(n_jobs=3)]: Done  42 out of  42 | elapsed:   26.6s finished


In [27]:
score_on_leaderboard = 0.73866275
print('Score on cross-validation: {}\nScore on leaderboard: {}\n DIFF: {}'.format(
    grid_search.best_score_, 
    score_on_leaderboard, 
    abs(grid_search.best_score_ - score_on_leaderboard)))

test_log['0'] = grid_search.best_estimator_.predict_proba(test_log.drop(['0'], axis=1))[:,1]
save_submission(test_log['0'], 'submission_logregression.csv')

Score on cross-validation: 0.7291972405052234
Score on leaderboard: 0.73866275
 DIFF: 0.009465509494776647


In [28]:
grid_search.best_estimator_

LogisticRegression(C=0.03, class_weight='balanced', dual=True,
          fit_intercept=True, intercept_scaling=1, max_iter=100,
          multi_class='ovr', n_jobs=1, penalty='l2', random_state=None,
          solver='liblinear', tol=0.0001, verbose=0, warm_start=False)

## Bagging by using logistic regression

In [29]:
bg = BaggingClassifier(base_estimator=grid_search.best_estimator_)
parameters = {'max_features': [0.9], 
              'max_samples': [0.9],
              'n_estimators' : [25, 15],
              'bootstrap_features' : [False]}
grid_search_bagging = GridSearchCV(bg, parameters, scoring ='roc_auc', cv=skf, error_score=1, n_jobs=n_jobs1)
grid_search_bagging = grid_search_bagging.fit(X=X, y=y)

In [30]:
score_on_leaderboard = 0.73504442
print('Score on bagging: {}\nScore on leaderboard: {}\n DIFF: {}'.format(
    grid_search_bagging.best_score_, 
    score_on_leaderboard, 
    abs(grid_search_bagging.best_score_ - score_on_leaderboard)))

test_['0'] = grid_search_bagging.best_estimator_.predict_proba(test_.drop(['0'], axis=1))[:, 1]
pd.DataFrame(test_['0']).to_csv('submission_bagging.csv')

Score on bagging: 0.729383679360034
Score on leaderboard: 0.73904442
 DIFF: 0.009660740639966026


## Random Forest

In [31]:
X = train_tree.drop(['0'], axis=1)
y = train_tree['0']

In [32]:
parameters = {'max_features': [0.1, .11], 
              'min_samples_leaf': [15],
              'max_depth': [32]}
rfc = RandomForestClassifier(random_state=11, n_estimators=100)
rfcv = GridSearchCV(rfc, parameters, n_jobs=n_jobs, cv=skf, verbose=1, scoring='roc_auc', error_score=1)
grid_search_rf = rfcv.fit(X, y)

Fitting 21 folds for each of 2 candidates, totalling 42 fits


[Parallel(n_jobs=3)]: Done  42 out of  42 | elapsed:  6.1min finished


In [33]:
score_on_leaderboard = 0.74315360
print('Score on random forest: {}\nScore on leaderboard: {}\n DIFF: {}'.format(
    rfcv.best_score_, 
    score_on_leaderboard, 
    abs(rfcv.best_score_ - score_on_leaderboard)))

test_tree['0'] = rfcv.best_estimator_.predict_proba(test_tree.drop(['0'], axis=1))[:,1]
save_submission(test_tree['0'], 'submission_random_forest.csv')

Score on random forest: 0.7374557011039021
Score on leaderboard: 0.7431536
 DIFF: 0.005697898896097842


In [34]:
grid_search_rf.best_estimator_

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=32, max_features=0.11, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=15, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=1,
            oob_score=False, random_state=11, verbose=0, warm_start=False)

## Simple ensemble

In [54]:
parameters = {'max_features': [0.11], 
              'min_samples_leaf': [15, 14],
              'max_depth': [32]}
etc = ExtraTreesClassifier(random_state=11, n_estimators=100)
etcv = GridSearchCV(etc, parameters, n_jobs=n_jobs, cv=skf, verbose=1, scoring='roc_auc', error_score=1)
grid_search_et = etcv.fit(X, y)

Fitting 21 folds for each of 2 candidates, totalling 42 fits


[Parallel(n_jobs=3)]: Done  42 out of  42 | elapsed:  6.1min finished


In [55]:
print('Score on random forest: {}'.format(grid_search_et.best_score_))

Score on random forest: 0.740079107942169


In [56]:
etcv.best_estimator_

ExtraTreesClassifier(bootstrap=False, class_weight=None, criterion='gini',
           max_depth=32, max_features=0.11, max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=14, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=1,
           oob_score=False, random_state=11, verbose=0, warm_start=False)

### XGBoost Classifier

In [42]:
xgb = XGBClassifier(random_state=11, n_estimators=150, max_depth=60, learning_rate=0.2, n_jobs=n_jobs)

In [43]:
grid_search_rf = rfcv.best_estimator_
grid_search_et = etcv.best_estimator_
grid_search_xgb = xgb
grid_search_lg = grid_search.best_estimator_
rf_predictions = []
et_predictions = []
xgb_predictions = []
lg_predictions = []

i = 1
for train, val in skf.split(X, y):
    print(i, 'random_forest', end=' ')
    grid_search_rf.fit(X.iloc[train], y[train])
    print('extra_trees', end=' ')
    grid_search_et.fit(X.iloc[train], y[train])
    print('xgboost', end=' ')
    grid_search_xgb.fit(X.iloc[train], y[train])
    print('logistic_regression', end=' ')
    grid_search_lg.fit(train_log.drop('0', axis=1).iloc[train], y[train])
    print('random_forest', end=' ')
    rf_predictions.append([y[val], grid_search_rf.predict_proba(X.iloc[val])[:,1]])
    print('extra_trees', end=' ')
    et_predictions.append([y[val], grid_search_et.predict_proba(X.iloc[val])[:,1]])
    print('xgboost', end=' ')
    xgb_predictions.append([y[val], grid_search_xgb.predict_proba(X.iloc[val])[:,1]])
    print('logistic_regression')
    lg_predictions.append([y[val], grid_search_lg.predict_proba(train_log.drop('0', axis=1).iloc[val])[:,1]])
    i += 1

1 random_forest extra_trees xgboost logistic regression random_forest extra_trees xgboost logistic_regression
2 random_forest extra_trees xgboost logistic regression random_forest extra_trees xgboost logistic_regression
3 random_forest extra_trees xgboost logistic regression random_forest extra_trees xgboost logistic_regression
4 random_forest extra_trees xgboost logistic regression random_forest extra_trees xgboost logistic_regression
5 random_forest extra_trees xgboost logistic regression random_forest extra_trees xgboost logistic_regression
6 random_forest extra_trees xgboost logistic regression random_forest extra_trees xgboost logistic_regression
7 random_forest extra_trees xgboost logistic regression random_forest extra_trees xgboost logistic_regression
8 random_forest extra_trees xgboost logistic regression random_forest extra_trees xgboost logistic_regression
9 random_forest extra_trees xgboost logistic regression random_forest extra_trees xgboost logistic_regression
10 random_

### Rank data

In [58]:
cv_score_rank = np.mean([roc_auc_score(rf_p[0],
                                       rankdata(rf_p[1]) + rankdata(et_p[1])) for rf_p, et_p in zip(rf_predictions, et_predictions)])
cv_score_rank

0.7414693559901894

### Weighted mean

In [59]:
scores = {}
for i in range(101):
    iter_ = 0.01 * i
    cv_score_weighted_mean = np.mean([roc_auc_score(rf_p[0],rf_p[1]* iter_ + et_p[1]*(1 - iter_)) for rf_p, et_p in zip(rf_predictions, et_predictions)])
    scores.update({cv_score_weighted_mean: iter_})
best_score = np.array(list(scores.keys())).max()
best_iter_ = scores.get(best_score)
best_score, best_iter_

(0.7417072765989441, 0.37)

In [60]:
rf_part = grid_search_rf.predict_proba(test_tree.drop(['0'], axis=1))[:,1]
et_part = grid_search_et.predict_proba(test_tree.drop(['0'], axis=1))[:,1]
lg_part = grid_search_lg.predict_proba(test_log.drop(['0'], axis=1))[:,1]
xgb_part = grid_search_xgb.predict_proba(test_tree.drop(['0'], axis=1))[:,1]

In [61]:
score_on_leaderboard = 0.74729373
print('Score on simple ensemble: {}\nScore on leaderboard: {}\n DIFF: {}'.format(
    best_score, 
    score_on_leaderboard, 
    abs(best_score - score_on_leaderboard)))

test_sub = rf_part * best_iter_ + et_part * (1 - best_iter_)
save_submission(test_sub , 'submission_simple_ensemble.csv')

Score on simple ensemble: 0.7417072765989441
Score on leaderboard: 0.74729373
 DIFF: 0.005586453401055902


## Stacking

In [62]:
X_stack = X.copy()
X_stack['rf'] = 0
X_stack['et'] = 0

test_stack = test_tree.copy()
test_stack['rf'] = rf_part
test_stack['et'] = et_part

for i, fold in enumerate(skf.split(X, y)):
    train, val = fold[0], fold[1]
    X_stack.iloc[val, -2] = rf_predictions[i][1]
    X_stack.iloc[val, -1] = et_predictions[i][1]

In [ ]:
parameters = {'max_features': [0.6, 0.7, 0.5, 0.4],
              'min_samples_leaf': [9, 7, 5],
              'max_depth': [13, 15, 20]}
etc = ExtraTreesClassifier(random_state=11, n_estimators=100, n_jobs=n_jobs)
etcv_stack = GridSearchCV(etc, parameters, n_jobs=n_jobs, cv=skf, verbose=1, scoring='roc_auc', error_score=1)
grid_search_et_stack = etcv_stack.fit(X_stack, y)

Fitting 21 folds for each of 36 candidates, totalling 756 fits


In [ ]:
score_on_leaderboard = 1 - 0.25669671
print('Score on stacking: {}\nScore on leaderboard: {}\n DIFF: {}'.format(
    grid_search_et_stack.best_score_, 
    score_on_leaderboard, 
    abs(grid_search_et_stack.best_score_ - score_on_leaderboard)))

test_tree['0'] = grid_search_et_stack.best_estimator_.predict_proba(test_stack.drop(['0'], axis=1))[:,1]
save_submission(test_tree['0'], 'submission_stacking.csv')

In [ ]:
grid_search_et_stack.best_estimator_

# Best solution

### Stack 1

In [ ]:
X_stack1 = X.copy()
X_stack1['rf'] = 0

test_stack1 = test_tree.copy()
test_stack1['rf'] = rf_part

for i, fold in enumerate(skf.split(X, y)):
    train, val = fold[0], fold[1]
    X_stack1.iloc[val, -1] = rf_predictions[i][1]

In [ ]:
parameters = {'max_features': [0.6, 0.7, 0.5, 0.4],
              'min_samples_leaf': [9, 7, 5],
              'max_depth': [13, 15, 20, 25]}
etc = ExtraTreesClassifier(random_state=11, n_estimators=100, n_jobs=n_jobs)
etcv_stack1 = GridSearchCV(etc, parameters, n_jobs=n_jobs, cv=skf, verbose=1, scoring='roc_auc', error_score=1)
grid_search_et_stack1 = etcv_stack1.fit(X_stack1, y)

### Stack 2

In [ ]:
X_stack2 = X.copy()
X_stack2['et'] = 0

test_stack2 = test_tree.copy()
test_stack2['et'] = et_part

for i, fold in enumerate(skf.split(X, y)):
    train, val = fold[0], fold[1]
    X_stack2.iloc[val, -1] = et_predictions[i][1]

In [ ]:
parameters = {'max_features': [0.6, 0.7, 0.5, 0.4],
              'min_samples_leaf': [9, 7, 5],
              'max_depth': [13, 15, 20, 25]}
etc = ExtraTreesClassifier(random_state=11, n_estimators=100, n_jobs=n_jobs)
etcv_stack2 = GridSearchCV(etc, parameters, n_jobs=n_jobs, cv=skf, verbose=1, scoring='roc_auc', error_score=1)
grid_search_et_stack2 = etcv_stack2.fit(X_stack2, y)

### Stack 3

In [ ]:
X_stack3 = X.copy()
X_stack3['xgb'] = 0

test_stack3 = test_tree.copy()
test_stack3['xgb'] = xgb_part

for i, fold in enumerate(skf.split(X, y)):
    train, val = fold[0], fold[1]
    X_stack3.iloc[val, -1] = xgb_predictions[i][1]

In [ ]:
parameters = {'max_features': [0.6, 0.7, 0.5, 0.4],
              'min_samples_leaf': [9, 7, 5],
              'max_depth': [13, 15, 20, 25]}
etc = ExtraTreesClassifier(random_state=11, n_estimators=100, n_jobs=n_jobs)
etcv_stack3 = GridSearchCV(etc, parameters, n_jobs=n_jobs, cv=skf, verbose=1, scoring='roc_auc', error_score=1)
grid_search_et_stack3 = etcv_stack3.fit(X_stack3, y)

### Stack 4

In [ ]:
X_stack4 = X.copy()
X_stack4['lg'] = 0

test_stack4 = test_tree.copy()
test_stack4['lg'] = lg_part

for i, fold in enumerate(skf.split(train_log.drop('0', axis=1), y)):
    train, val = fold[0], fold[1]
    X_stack4.iloc[val, -1] = lg_predictions[i][1]

In [ ]:
parameters = {'max_features': [0.6, 0.7, 0.5, 0.4],
              'min_samples_leaf': [9, 7, 5],
              'max_depth': [13, 15, 20, 25]}
etc = ExtraTreesClassifier(random_state=11, n_estimators=100, n_jobs=n_jobs)
etcv_stack4 = GridSearchCV(etc, parameters, n_jobs=n_jobs, cv=skf, verbose=1, scoring='roc_auc', error_score=1)
grid_search_et_stack4 = etcv_stack4.fit(X_stack4, y)

## Ensemble of stacking

In [ ]:
grid_search_et_stack1 = grid_search_et_stack1.best_estimator_
grid_search_et_stack2 = grid_search_et_stack2.best_estimator_
grid_search_et_stack3 = grid_search_et_stack3.best_estimator_
grid_search_et_stack4 = grid_search_et_stack4.best_estimator_
stack1_predictions = []
stack2_predictions = []
stack3_predictions = []
stack4_predictions = []

i = 1
for train, val in skf.split(X, y):
    print(i, 'Fitting:', 'stack_1', end=' ')
    grid_search_et_stack1.fit(X_stack1.iloc[train], y[train])
    print('stack_2', end=' ')
    grid_search_et_stack2.fit(X_stack2.iloc[train], y[train])
    print('stack_3', end=' ')
    grid_search_et_stack3.fit(X_stack3.iloc[train], y[train])
    print('stack_4', end=' ')
    grid_search_et_stack4.fit(X_stack4.iloc[train], y[train])
    print('Predicting:', 'stack_1', end=' ')
    stack1_predictions.append([y[val], grid_search_et_stack1.predict_proba(X_stack1.iloc[val])[:,1]])
    print('stack_2', end=' ')
    stack2_predictions.append([y[val], grid_search_et_stack2.predict_proba(X_stack2.iloc[val])[:,1]])
    print('stack_3', end=' ')
    stack3_predictions.append([y[val], grid_search_et_stack3.predict_proba(X_stack3.iloc[val])[:,1]])
    print('stack_4')
    stack4_predictions.append([y[val], grid_search_et_stack4.predict_proba(X_stack4.iloc[val])[:,1]])
    i+=1

In [ ]:
scores = {}
for i1 in range(21):
    iter_1 = i1 * 0.05
    for i2 in range(21 - i1):
        iter_2 = i2 * 0.05
        for i3 in range(21 - i1 - i2):
            iter_3 = i3 * 0.05
            iter_4 = 1 - iter_1 -iter_2 -iter_3
            cv_score_weighted_mean = np.mean([roc_auc_score(st1[0], st1[1] * iter_1 + st2[1] * iter_2 + st3[1] * iter_3 + st4[1] * iter_4) for st1, st2, st3, st4 in zip(stack1_predictions, stack2_predictions, stack3_predictions, stack4_predictions)])
            scores.update({cv_score_weighted_mean: [iter_1, iter_2, iter_3, iter_4]}) 
best_score = np.array(list(scores.keys())).max()
best_iters_ = scores.get(best_score)
best_score, best_iters_

In [ ]:
stack1_part = grid_search_et_stack1.predict_proba(test_stack1.drop(['0'], axis=1))[:,1]
stack2_part = grid_search_et_stack2.predict_proba(test_stack2.drop(['0'], axis=1))[:,1]
stack3_part = grid_search_et_stack3.predict_proba(test_stack3.drop(['0'], axis=1))[:,1]
stack4_part = grid_search_et_stack4.predict_proba(test_stack4.drop(['0'], axis=1))[:,1]

In [ ]:
score_on_leaderboard = 0.74729373
print('Score on best solution: {}\nScore on leaderboard: {}\n DIFF: {}'.format(
    best_score, 
    score_on_leaderboard, 
    abs(best_score - score_on_leaderboard)))

test_sub_stac = stack1_part * best_iters_[0] + stack2_part * best_iters_[1] + stack3_part * best_iters_[2] + stack4_part * best_iters_[3]
save_submission(test_sub_stac , 'submission_best_solution_i_hope.csv')

##  The end